In [1]:
!pip install --quiet cartopy netcdf4 earthaccess scipy zipfile36

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 11.6/11.6 MB 38.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 5.5/5.5 MB 53.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 57.1/57.1 kB 2.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 28.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 76.6/76.6 kB 2.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 316.1/316.1 kB 15.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 12.2/12.2 MB 39.0 MB/s eta 0:00:00
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
torch 2.3.0+cu121 requires nvidia-cublas-cu12==12.1.3.1; platform_system == "Linux" and platform_machine == "x86_64", which is not installed.
torch 2.3.0+cu121 requires nvidia-cuda-cupti-cu12==12.1.105; platform_system == "Linux" and platform_machine == "x86_64"

In [2]:
import datetime
from datetime import date

from pathlib import Path

from zipfile import ZipFile

import earthaccess

import xarray as xr

from netCDF4 import Dataset

import requests

import numpy as np

import matplotlib as mpl
from matplotlib import pyplot as plt
import matplotlib.ticker as ticker

import cartopy.feature as cfeature
from cartopy import crs as ccrs

from PIL import Image

import os
from scipy.io import savemat
from google.colab import files as colab
import zipfile
import time

In [3]:
if not os.path.exists('/content/data_files'):
  Path('/content/data_files').mkdir()

if not os.path.exists('/content/temp_data'):
  Path('/content/temp_data').mkdir()

data_path = Path('/content/data_files')
temp_path = Path('/content/temp_data')

In [11]:
auth = earthaccess.login(strategy='interactive')

Enter your Earthdata Login username: tely136
Enter your Earthdata password: ··········


In [12]:
auto = False

In [13]:
short_name = 'TEMPO_NO2_L2'
if auto == True:
  observation_start = '2023-08-01 00:00:00'  # 'YYYY-MM-DD HH:MM:SS'
  observation_end = '2024-8-31 23:59:59' # 'YYYY-MM-DD HH:MM:SS'

  lat_min = 39
  lat_max = 44

  lon_min = -77
  lon_max = -70
  bbox = (lon_min, lat_min, lon_max, lat_max)

  # Search NASA Earthdata for TEMPO NO2 granules files
  results = earthaccess.search_data(short_name=short_name,
                                    temporal=(observation_start, observation_end),
                                    bounding_box=bbox)

In [27]:
short_name = 'TEMPO_NO2_L2'
lat_min = 39
lat_max = 44

lon_min = -77
lon_max = -70
bbox = (lon_min, lat_min, lon_max, lat_max)

results = []
download_list = [20230802, 20230809, 20230816, 20230821, 20230822, 20230823, 20230825, 20230826, 20231217, 20231218, 20231219, 20231220, 20231221, 20231222, 20231223, 20231224, 20231225, 20231226, 20231227, 20231228, 20231229, 20231230]
if auto == False:
  for date in download_list:
    observation_start = datetime.datetime.strptime(str(date), '%Y%m%d') + datetime.timedelta(hours=14)
    observation_end = observation_start + datetime.timedelta(hours = 4)
    temp_results = earthaccess.search_data(short_name=short_name,
                                      temporal=(observation_start, observation_end),
                                      bounding_box=bbox)

    if temp_results != []:
      for granule in temp_results:
        results.append(granule)

Granules found: 9
Granules found: 12
Granules found: 12
Granules found: 12
Granules found: 12
Granules found: 0
Granules found: 12
Granules found: 9
Granules found: 9
Granules found: 9
Granules found: 9
Granules found: 9
Granules found: 8
Granules found: 8
Granules found: 8
Granules found: 8
Granules found: 8
Granules found: 6
Granules found: 8
Granules found: 8
Granules found: 8
Granules found: 4


In [28]:
overwrite = True
if overwrite == True:
  for file in os.listdir(data_path):
    os.remove(Path(data_path, file))

In [29]:
def download_with_retries(url, retries, delay):
  for attempt in range(retries):
    try:
      response = earthaccess.download(url, local_path=temp_path)
      print(response)
      if not (response == []):
        return response

      else:
        print(f"Failed to download {url}")

    except Exception as e:
        print(f"Error downloading {url}: {e}")

    time.sleep(delay)

  print(f"Failed to download {url} after {retries} attempts")
  return None




In [32]:
i = 1
for granule in results:
  for file in os.listdir(temp_path):
      if file.endswith('.nc'):
        os.remove(Path(temp_path,file))

  print(f'Downloading file {i} of {len(results)}')
  #try:
  #earthaccess.download(granule, local_path=temp_path)
  file_content = download_with_retries(granule, 3, 5)

  lat_slice = slice(lat_min, lat_max)
  lon_slice = slice(lon_min, lon_max)

  file_name = os.listdir(temp_path)
  file_path = os.path.join(temp_path, file_name[0])

  dataset = Dataset(file_path, 'r')
  product = dataset.groups['product']
  geolocation = dataset.groups['geolocation']
  support_data = dataset.groups['support_data']

  lat = geolocation.variables['latitude'][:]
  lon = geolocation.variables['longitude'][:]


  region_mask = np.where((lat>=lat_min) & (lat<=lat_max) & (lon>=lon_min) & (lon<=lon_max))

  if any(element.size==0 for element in region_mask):
    print('No data in bounds, skipping iteration')
    continue

  row_min = min(region_mask[0])
  row_max = max(region_mask[0])
  col_min = min(region_mask[1])
  col_max = max(region_mask[1])


  lat = geolocation.variables['latitude']
  lon = geolocation.variables['longitude']
  time = geolocation.variables['longitude']
  solar_zenith = geolocation.variables['solar_zenith_angle']
  solar_azimuth = geolocation.variables['solar_azimuth_angle']
  viewing_zenith = geolocation.variables['viewing_zenith_angle']
  viewing_azimuth = geolocation.variables['viewing_azimuth_angle']

  no2 = product.variables['vertical_column_troposphere']
  qa = product.variables['main_data_quality_flag']

  albedo = support_data.variables['albedo']
  eff_cld = support_data.variables['eff_cloud_fraction']
  snow_ice = support_data.variables['snow_ice_fraction']


  lat_subset = lat[row_min:row_max+1, col_min:col_max+1].astype(np.float64)
  lon_subset = lon[row_min:row_max+1, col_min:col_max+1].astype(np.float64)
  time_subset = time[row_min:row_max+1]
  sza_subset = solar_zenith[row_min:row_max+1, col_min:col_max+1].astype(np.float64)

  no2_subset = no2[row_min:row_max+1, col_min:col_max+1].astype(np.float64)
  qa_subset = qa[row_min:row_max+1, col_min:col_max+1].astype(np.float64)

  albedo_subset = albedo[row_min:row_max+1, col_min:col_max+1].astype(np.float64)
  eff_cld_subset = eff_cld[row_min:row_max+1, col_min:col_max+1].astype(np.float64)
  snow_ice_subset = snow_ice[row_min:row_max+1, col_min:col_max+1].astype(np.float64)

  no2_subset = np.where((no2_subset<0) | (no2_subset>pow(10,36)), np.nan, no2_subset)

  save_data = {
      'no2': no2_subset,
      'lat': lat_subset,
      'lon': lon_subset,
      'time': time_subset,
      'sza': sza_subset,
      'qa': qa_subset,
      'albedo': albedo_subset,
      'eff_cld': eff_cld_subset,
      'snow_ice': snow_ice_subset
  }
  save_name = str(file_name[0]).replace('.nc', '') + '.mat'

  savemat(os.path.join(data_path, save_name), save_data)

  i = i + 1

  os.remove(file_path)

 Getting 1 granules, approx download size: 0.0 GB


QUEUEING TASKS | :   0%|          | 0/1 [00:00<?, ?it/s]

PROCESSING TASKS | :   0%|          | 0/1 [00:00<?, ?it/s]

COLLECTING RESULTS | :   0%|          | 0/1 [00:00<?, ?it/s]

['/content/temp_data/TEMPO_NO2_L2_V01_20230802T151902Z_S001G02.nc']
 Getting 1 granules, approx download size: 0.0 GB


...

['/content/temp_data/TEMPO_NO2_L2_V01_20231230T151749Z_S004G02.nc']
 Getting 1 granules, approx download size: 0.0 GB


QUEUEING TASKS | :   0%|          | 0/1 [00:00<?, ?it/s]

PROCESSING TASKS | :   0%|          | 0/1 [00:00<?, ?it/s]

COLLECTING RESULTS | :   0%|          | 0/1 [00:00<?, ?it/s]

['/content/temp_data/TEMPO_NO2_L2_V01_20231230T152429Z_S004G03.nc']


In [33]:
zip_filename = 'my_files.zip'
with zipfile.ZipFile(zip_filename, 'w') as zipf:
    for root, dirs, files in os.walk(data_path):
        for file in files:
            zipf.write(os.path.join(root, file), os.path.relpath(os.path.join(root, file), 'my_files'))

# Download the zip file
colab.download(zip_filename)

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>